In [30]:
!python -m pip install openpyxl

  Using cached openpyxl-3.1.5-py2.py3-none-any.whl.metadata (2.5 kB)
  Using cached et_xmlfile-2.0.0-py3-none-any.whl.metadata (2.7 kB)
Using cached openpyxl-3.1.5-py2.py3-none-any.whl (250 kB)
Using cached et_xmlfile-2.0.0-py3-none-any.whl (18 kB)


### 캡셔닝 결과 취합

In [31]:
import re
import json
from typing import Any, Dict, Optional

# — 후처리용 유틸 함수들 —
def _process_objects(field: Any) -> Optional[list]:
    if field is None:
        return None
    if isinstance(field, list):
        return field or None
    text = str(field).strip()
    if text.lower().startswith("unable to identify"):
        return None
    items = [p.strip() for p in text.split(",") if p.strip()]
    return items or None

def _process_parts(field: Any) -> Optional[list]:
    if field is None:
        return None
    if isinstance(field, list):
        return field or None
    text = str(field).strip()
    if text.lower().startswith("unable to determine"):
        return None
    # 각 줄을 분리해서, "- " 로 시작하는 부분만 내용만 취함
    lines = [line.strip() for line in text.splitlines() if line.strip()]
    items = []
    for line in lines:
        m = re.match(r"^-+\s*(.*)", line)
        if m:
            items.append(m.group(1).strip())
        else:
            # 혹시 dash 없이 바로 문장만 있을 때
            items.append(line)
    return items or None

def parse_caption(caption_text: str) -> Dict[str, Optional[Any]]:
    # 1) JSON 블록 우선 파싱
    m = re.search(r"```json\s*(\{.*?\})\s*```", caption_text, re.DOTALL)
    if m:
        try:
            data = json.loads(m.group(1))
            return {
                "Status": data.get("Status"),
                "Caption": data.get("Caption"),
                "Objects": _process_objects(data.get("Objects")),
                "Parts and Relationships": _process_parts(data.get("Parts and Relationships"))
            }
        except json.JSONDecodeError:
            pass

    # 2) 헤더 기반 섹션 분리
    header_pat = r"\*{0,2}\s*(Status|Caption|Objects|Parts and Relationships)\s*\*{0,2}\s*:\s*"
    matches = [(h.group(1), h.start()) for h in re.finditer(header_pat, caption_text, re.IGNORECASE)]
    matches.sort(key=lambda x: x[1])
    raw = {"Status": None, "Caption": None, "Objects": None, "Parts and Relationships": None}

    for i, (sec, start) in enumerate(matches):
        end = matches[i+1][1] if i+1 < len(matches) else len(caption_text)
        hdr_end = re.search(header_pat, caption_text[start:], re.IGNORECASE).end() + start
        cnt = caption_text[hdr_end:end]
        # 앞뒤 **, 공백, 개행 제거
        cnt = re.sub(r"^[\*\s\r\n]+", "", cnt)
        cnt = re.sub(r"[\*\s\r\n]+$", "", cnt)
        raw[sec] = cnt

    # 3) Objects / Parts 후처리
    raw["Objects"] = _process_objects(raw["Objects"])
    raw["Parts and Relationships"] = _process_parts(raw["Parts and Relationships"])
    return raw

- 렌더링용 블렌더 호출 코드

In [76]:
import subprocess
from pathlib import Path

def run_blender(mesh_dir: str, output_dir: str,
                blender_path: str = "./blender-3.4.1-linux-x64/blender",
                script_relpath: str = "../src/ys/blender_render_script_type1.py"):
    base_dir = Path.cwd()

    # Blender 실행파일 절대경로
    # blender_exec = Path(blender_path).resolve()
    blender_exec = Path(blender_path)
    # 스크립트 절대경로
    script_path = (base_dir / script_relpath).resolve()

    if not script_path.exists():
        raise FileNotFoundError(f"스크립트를 찾을 수 없습니다: {script_path}")

    # mesh_dir, output_dir 절대경로로 변환
    mesh_abs = Path(mesh_dir).resolve()
    out_abs  = Path(output_dir).resolve()
    if not mesh_abs.exists():
        raise FileNotFoundError(f"메쉬 파일을 찾을 수 없습니다: {mesh_abs}")
    
    # 출력 디렉토리는 미리 만들어 두는 편이 안전
    out_abs.mkdir(parents=True, exist_ok=True)

    cmd = [
        str(blender_exec),
        "-b",
        "-P", str(script_path),
        "--",
        "--mesh_dir", str(mesh_abs),
        "--output_dir", str(out_abs)
    ]
    print(cmd)

    try:
        result = subprocess.run(
            cmd,
            check=True,
            capture_output=True,
            text=True,
            cwd=base_dir
        )
        print("=== Blender stdout ===")
        print(result.stdout)
        print("=== Blender stderr ===")
        print(result.stderr)
    except subprocess.CalledProcessError as e:
        print(f"Blender 실행에 실패했습니다 (return code: {e.returncode})")
        print("stdout:", e.stdout)
        print("stderr:", e.stderr)
        raise

- 분할된 파트에 대해 렌더링하고, 경로를 옮기는 모듈
- 개선사항
    - 현재는 고정된 뷰의 8개의 이미지만 받음. 섞어서 받을 수 있게 해야 

In [90]:
import random
import shutil
from pathlib import Path
from PIL import Image
import logging
from typing import Tuple

log = logging.getLogger(__name__)

class RenderCollageUtils:
    @staticmethod
    def create_and_move_render_collage(
        mesh_dir: Path,
        renders_root: Path,
        target_res: Tuple[int, int] = (2048, 2048),
    ) -> None:
        """
        1) mesh_dir(renders/{mesh-id}) 하위의 8개 PNG를 읽어서 3x3 콜라주 생성.
           - 8개 중 랜덤으로 하나를 복제해 9개로 만듦.
        2) 완성된 콜라주 이미지를 renders_root (renders/) 에 저장.
        3) 원본 mesh_dir 디렉토리를 통째로 삭제.

        :param mesh_dir: renders/{mesh-id} 디렉토리
        :param renders_root: 상위 renders/ 디렉토리
        :param target_res: 콜라주 전체 해상도 (width, height)
        """
        # 1) 입력 디렉토리 검사
        if not mesh_dir.exists() or not mesh_dir.is_dir():
            log.warning("Mesh directory %s does not exist or is not a directory.", mesh_dir)
            return

        # 2) PNG 목록 수집 (오직 '00020.png' 같은 5자리 숫자 파일만)
        import re
        pattern = re.compile(r"^\d{5}\.png$")  
        png_files = [p for p in mesh_dir.iterdir() 
                    if p.is_file() and pattern.match(p.name)]
        png_files.sort()  # 이름순 정렬
        if len(png_files) != 8:
            log.warning("Expected exactly 8 view-png (e.g. 00020.png–00027.png) in %s, but found %d. Aborting.",
                        mesh_dir, len(png_files))
            return

        # 3) 8개 중 하나를 랜덤 복제하여 9개 리스트 구성
        #    (원본 리스트를 복사한 뒤, 랜덤 선택파일을 append)
        collage_files = png_files.copy()
        duplicate = random.choice(png_files)
        collage_files.append(duplicate)

        # 4) 캔버스 및 셀 크기 계산 (3x3)
        canvas_w, canvas_h = target_res
        cell_w, cell_h = canvas_w // 3, canvas_h // 3
        canvas = Image.new("RGB", (canvas_w, canvas_h))

        # 5) 9개 이미지 순서대로 붙이기
        for idx, img_path in enumerate(collage_files):
            img = Image.open(img_path).convert("RGB").resize((cell_w, cell_h), Image.LANCZOS)
            row, col = divmod(idx, 3)
            canvas.paste(img, (col * cell_w, row * cell_h))

        # 6) 출력 파일명 및 저장 경로
        mesh_id = mesh_dir.name
        out_name = f"{mesh_id}_collage_{canvas_w}x{canvas_h}.png"
        out_path = renders_root / out_name
        canvas.save(out_path)
        log.info("Saved render collage %s", out_path)

        # 7) 원본 디렉토리 통째로 삭제
        try:
            shutil.rmtree(mesh_dir)
            log.info("Removed mesh directory %s", mesh_dir)
        except Exception as e:
            log.error("Failed to remove directory %s: %s", mesh_dir, e)

In [92]:
import os
import json
import shutil
from pathlib import Path
from tqdm import tqdm
import pandas as pd  # 추가
from openpyxl.styles import Alignment
import trimesh
from pathlib import Path
# from trimesh import Trimesh, Scene

base_dir = "../outputs/mesh_segmentation_output/CustomDataset"
origin_base_dir = "../assets/CustomDataset_Completed"
obj_dir = "000-001"
json_file = f"{base_dir}/{obj_dir}_status.json"
TARGET_DIR = Path(f"{base_dir}/{obj_dir}/")
ORIGIN_DIR = Path(f"{origin_base_dir}/{obj_dir}/")

# 1) JSON 한 번 로드
with open(json_file, 'r', encoding='utf-8') as f:
    status_data = json.load(f)

cnt = 0
target = 20
rows = []
# 2) mesh 디렉터리 목록
mesh_dirs = sorted(d for d in TARGET_DIR.iterdir() if d.is_dir())
for mesh_dir in tqdm(mesh_dirs, desc="Reading captions"):
    # temp
    # if target <= cnt:
    #     break
    
    mesh_id = mesh_dir.name

    # 해당 mesh_id의 caption 상태 정보 가져오기
    entry = status_data.get(mesh_id, {})
    caps  = entry.get("captions", {})
    gpt_flag    = caps.get("gpt", False)
    gemma_flag  = caps.get("gemma", False)

    # 우선순위에 따른 파일명 결정
    if (gpt_flag ^ gemma_flag):  # 둘 중 하나만 True
        chosen = "caption_gemma.txt" if gemma_flag else "caption_gpt.txt"
    else:  # 둘 다 True 이거나 둘 다 False
        chosen = "caption_gpt.txt"
        
    path = mesh_dir / chosen
    # if not path.exists():
    #     print(f"[{mesh_id}] ⚠️ {chosen} not found")
    #     continue
    if not path.exists():
        print(f"[{mesh_id}] ⚠️ {chosen} not found")
        status = entry.get("render", False)
        rows.append({
            "mesh_id": mesh_id,
            "status": status,
            "read_file": None,
            "caption_text": None,
            "Caption": None,
            "Objects": None,
            "Parts and Relationships": None
        })
        continue
    
    glb_pattern = f"{mesh_id}_label_*.glb"
    glbs_list = sorted(mesh_dir.glob(glb_pattern))

    # 3) 실제 존재하는 캡션 파일 경로 찾기
    caption_path = mesh_dir / chosen
    if caption_path.exists():
        caption_text = caption_path.read_text(encoding='utf-8').strip()
        print(f"[{mesh_id}] -> 읽은 파일: {chosen}, 내용 길이: {len(caption_text)}")
        # TODO: caption_text 사용하여 다음 파이프라인 수행
    else:
        print(f"[{mesh_id}] 경고: {chosen} 파일이 없습니다. captions_list: {sorted(p.name for p in mesh_dir.glob('caption_*.txt'))}")
    
    
    parsed = parse_caption(caption_text)
    rows.append({
        "mesh_id": mesh_id,
        "status": entry.get("render", False),
        "read_file": chosen,
        "caption_text": caption_text,
        "Caption": parsed["Caption"],
        "Objects": parsed["Objects"],
        "Parts and Relationships": parsed["Parts and Relationships"]
    })
    
    origin_mesh_path = ORIGIN_DIR / mesh_id / f"{mesh_id}.obj"
    origin_mesh = trimesh.load(origin_mesh_path)
    num_of_origin_faces = origin_mesh.faces.shape[0]
    
    # next: 각 glb에 대해 렌더 → collage → LLM 캡셔닝 …
    # print(rows)
    for glb in tqdm(glbs_list, desc="Processing glb files"):
        print(glb)
        scene = trimesh.load(glb)
        
        geometries = list(scene.geometry.values())
        num_of_glb_faces = geometries[0].faces.shape[0]
        
        # Origin face와 비교해서 n% 이하이면 pass(너무 작은 파트임), m% 이상이면 pass(원본과 너무 같음)
        # 이거 너무 Rule based 접근법이긴 함
        overlap_ratio = num_of_glb_faces / num_of_origin_faces
        print(f"[{mesh_id}] 면적 비율: {overlap_ratio:.2%}")
        if overlap_ratio < 0.1 or overlap_ratio > 0.75:
            print(f"[{mesh_id}] ⚠️ {glb.name} 면적 비율 {overlap_ratio:.2%}으로 패스")
            continue
        
        print(f"[{mesh_id}] 렌더링 중: {glb.name}")
        target_output_dir = f"{TARGET_DIR}/{mesh_id}/renders"
        run_blender(
            mesh_dir=glb,
            output_dir=target_output_dir,
            blender_path="./blender-3.4.1-linux-x64/blender",
            script_relpath="blender_render_script_type1.py"
        )
        # render 디렉토리에 있는 결과물 모아서 2048x2048 이미지로 만들고 하위 디렉토리 지우기
        renders_root = Path(target_output_dir)
        mesh_dir = renders_root / glb.stem   # 예: renders/000123 에 8개의 png가 있을 때
        RenderCollageUtils.create_and_move_render_collage(
            mesh_dir=mesh_dir,
            renders_root=renders_root,
            target_res=(2048, 2048)
        )
    
    # next
    # 각 glb 파일에 대해 렌더 수행하고, 이것도 9장을 하나로 합축하는 코드 재활용
    # 그리고 전체 caption을 주고, 해당 렌더 이미지는 segmented된 파트 중 하나에 해당한다고 언급
    # 최종 캡션 획득
    # cnt += 1
    
    
    # break
    
# # DataFrame으로 변환
# df = pd.DataFrame(rows, columns=[
#     "mesh_id","status","read_file","caption_text","Caption","Objects","Parts and Relationships"
# ])

# # 엑셀로 쓰면서 스타일링
# output_path = Path(base_dir) / f"{obj_dir}_captions_summary.xlsx"
# with pd.ExcelWriter(output_path, engine="openpyxl") as writer:
#     df.to_excel(writer, index=False, sheet_name="Summary")
#     ws = writer.sheets["Summary"]

#     # 컬럼 너비
#     ws.column_dimensions["A"].width = 38   # mesh_id
#     ws.column_dimensions["C"].width = 14   # read_file
#     ws.column_dimensions["D"].width = 115  # caption_text
#     ws.column_dimensions["E"].width = 140  # Caption
#     ws.column_dimensions["F"].width = 40   # Objects
#     ws.column_dimensions["G"].width = 70   # Parts and Relationships

#     # 정렬 & wrap 설정
#     # A: mesh_id center
#     for cell in ws["A"]:
#         cell.alignment = Alignment(horizontal="center", wrap_text=False)
#     # C: read_file center
#     for cell in ws["C"]:
#         cell.alignment = Alignment(horizontal="center", wrap_text=False)
#     # D, E, G: wrap text
#     for col in ("D","E","G"):
#         for cell in ws[col]:
#             cell.alignment = Alignment(wrap_text=True)

# print("Saved styled Excel to:", output_path)

Reading captions:  68%|██████▊   | 264/386 [14:40<12:09,  5.98s/it]

=== Blender stdout ===
Blender 3.4.1 (hash 55485cb379f7 built 2022-12-20 00:46:45)
/run/user/1000/gvfs/ non-existent directory
/home/user/ys/mesh_reasoning/samesh/outputs/mesh_segmentation_output/CustomDataset/000-001/b10270c90fbb43a3a70a9e3f1c27c073/b10270c90fbb43a3a70a9e3f1c27c073_label_35.glb
['/home/user/ys/mesh_reasoning/samesh/outputs/mesh_segmentation_output/CustomDataset/000-001/b10270c90fbb43a3a70a9e3f1c27c073/b10270c90fbb43a3a70a9e3f1c27c073_label_35.glb']
Data are loaded, start creating Blender stuff
glTF import finished in 0.00s
begin*************
curpath: /home/user/ys/mesh_reasoning/samesh/outputs/mesh_segmentation_output/CustomDataset/000-001/b10270c90fbb43a3a70a9e3f1c27c073/renders/b10270c90fbb43a3a70a9e3f1c27c073_label_35
Fra:1 Mem:19.45M (Peak 20.57M) | Time:00:00.06 | Syncing Light
Fra:1 Mem:19.45M (Peak 20.57M) | Time:00:00.06 | Syncing Camera
Fra:1 Mem:19.45M (Peak 20.57M) | Time:00:00.06 | Syncing world
Fra:1 Mem:19.45M (Peak 20.57M) | Time:00:00.06 | Syncing geom

../outputs/mesh_segmentation_output/CustomDataset/000-001/b19f072a65c847038a9b0bfdf5945452/b19f072a65c847038a9b0bfdf5945452_label_155.glb
[b19f072a65c847038a9b0bfdf5945452] 면적 비율: 0.43%
[b19f072a65c847038a9b0bfdf5945452] ⚠️ b19f072a65c847038a9b0bfdf5945452_label_155.glb 면적 비율 0.43%으로 패스
../outputs/mesh_segmentation_output/CustomDataset/000-001/b19f072a65c847038a9b0bfdf5945452/b19f072a65c847038a9b0bfdf5945452_label_162.glb
[b19f072a65c847038a9b0bfdf5945452] 면적 비율: 3.45%
[b19f072a65c847038a9b0bfdf5945452] ⚠️ b19f072a65c847038a9b0bfdf5945452_label_162.glb 면적 비율 3.45%으로 패스
../outputs/mesh_segmentation_output/CustomDataset/000-001/b19f072a65c847038a9b0bfdf5945452/b19f072a65c847038a9b0bfdf5945452_label_243.glb
[b19f072a65c847038a9b0bfdf5945452] 면적 비율: 44.61%
[b19f072a65c847038a9b0bfdf5945452] 렌더링 중: b19f072a65c847038a9b0bfdf5945452_label_243.glb
['blender-3.4.1-linux-x64/blender', '-b', '-P', '/home/user/ys/mesh_reasoning/samesh/notebooks/blender_render_script_type1.py', '--', '--mesh_dir', 

=== Blender stdout ===
Blender 3.4.1 (hash 55485cb379f7 built 2022-12-20 00:46:45)
/run/user/1000/gvfs/ non-existent directory
/home/user/ys/mesh_reasoning/samesh/outputs/mesh_segmentation_output/CustomDataset/000-001/b19f072a65c847038a9b0bfdf5945452/b19f072a65c847038a9b0bfdf5945452_label_243.glb
['/home/user/ys/mesh_reasoning/samesh/outputs/mesh_segmentation_output/CustomDataset/000-001/b19f072a65c847038a9b0bfdf5945452/b19f072a65c847038a9b0bfdf5945452_label_243.glb']
Data are loaded, start creating Blender stuff
glTF import finished in 0.00s
begin*************
curpath: /home/user/ys/mesh_reasoning/samesh/outputs/mesh_segmentation_output/CustomDataset/000-001/b19f072a65c847038a9b0bfdf5945452/renders/b19f072a65c847038a9b0bfdf5945452_label_243
Fra:1 Mem:19.57M (Peak 20.70M) | Time:00:00.06 | Syncing Light
Fra:1 Mem:19.57M (Peak 20.70M) | Time:00:00.06 | Syncing Camera
Fra:1 Mem:19.57M (Peak 20.70M) | Time:00:00.06 | Syncing world
Fra:1 Mem:19.58M (Peak 20.70M) | Time:00:00.06 | Syncing g

Reading captions:  69%|██████▊   | 265/386 [14:45<11:45,  5.83s/it]

...

../outputs/mesh_segmentation_output/CustomDataset/000-001/ff9fb3fc5bfa4fa19a4e8f07141fa4df/ff9fb3fc5bfa4fa19a4e8f07141fa4df_label_101.glb
[ff9fb3fc5bfa4fa19a4e8f07141fa4df] 면적 비율: 0.88%
[ff9fb3fc5bfa4fa19a4e8f07141fa4df] ⚠️ ff9fb3fc5bfa4fa19a4e8f07141fa4df_label_101.glb 면적 비율 0.88%으로 패스
../outputs/mesh_segmentation_output/CustomDataset/000-001/ff9fb3fc5bfa4fa19a4e8f07141fa4df/ff9fb3fc5bfa4fa19a4e8f07141fa4df_label_102.glb
[ff9fb3fc5bfa4fa19a4e8f07141fa4df] 면적 비율: 0.44%
[ff9fb3fc5bfa4fa19a4e8f07141fa4df] ⚠️ ff9fb3fc5bfa4fa19a4e8f07141fa4df_label_102.glb 면적 비율 0.44%으로 패스
../outputs/mesh_segmentation_output/CustomDataset/000-001/ff9fb3fc5bfa4fa19a4e8f07141fa4df/ff9fb3fc5bfa4fa19a4e8f07141fa4df_label_104.glb
[ff9fb3fc5bfa4fa19a4e8f07141fa4df] 면적 비율: 0.88%
[ff9fb3fc5bfa4fa19a4e8f07141fa4df] ⚠️ ff9fb3fc5bfa4fa19a4e8f07141fa4df_label_104.glb 면적 비율 0.88%으로 패스
../outputs/mesh_segmentation_output/CustomDataset/000-001/ff9fb3fc5bfa4fa19a4e8f07141fa4df/ff9fb3fc5bfa4fa19a4e8f07141fa4df_label_106.gl

Processing glb files: 100%|██████████| 1/1 [00:00<00:00, 1860.00it/s]


../outputs/mesh_segmentation_output/CustomDataset/000-001/y0KSBqo8lcEnAwqYkI29kgHCUn4/y0KSBqo8lcEnAwqYkI29kgHCUn4_label_40.glb
[y0KSBqo8lcEnAwqYkI29kgHCUn4] 면적 비율: 100.00%
[y0KSBqo8lcEnAwqYkI29kgHCUn4] ⚠️ y0KSBqo8lcEnAwqYkI29kgHCUn4_label_40.glb 면적 비율 100.00%으로 패스
[ydSFQC0HWE7eMaulss0Xak4pe1X] -> 읽은 파일: caption_gpt.txt, 내용 길이: 123


Reading captions: 100%|██████████| 386/386 [20:01<00:00,  3.11s/it]

../outputs/mesh_segmentation_output/CustomDataset/000-001/ydSFQC0HWE7eMaulss0Xak4pe1X/ydSFQC0HWE7eMaulss0Xak4pe1X_label_40.glb
[ydSFQC0HWE7eMaulss0Xak4pe1X] 면적 비율: 100.00%
[ydSFQC0HWE7eMaulss0Xak4pe1X] ⚠️ ydSFQC0HWE7eMaulss0Xak4pe1X_label_40.glb 면적 비율 100.00%으로 패스


In [ ]:
# 테스트 코드
print(TARGET_DIR)

origin_base_dir = "../assets/CustomDataset"

../outputs/mesh_segmentation_output/CustomDataset/000-001


In [ ]:
import subprocess
from pathlib import Path

def run_blender(mesh_dir: str, output_dir: str,
                blender_path: str = "./blender-3.4.1-linux-x64/blender",
                script_relpath: str = "../src/ys/blender_render_script_type1.py"):
    base_dir = Path.cwd()

    # Blender 실행파일 절대경로
    # blender_exec = Path(blender_path).resolve()
    blender_exec = Path(blender_path)
    # 스크립트 절대경로
    script_path = (base_dir / script_relpath).resolve()

    if not script_path.exists():
        raise FileNotFoundError(f"스크립트를 찾을 수 없습니다: {script_path}")

    # mesh_dir, output_dir 절대경로로 변환
    mesh_abs = Path(mesh_dir).resolve()
    out_abs  = Path(output_dir).resolve()
    if not mesh_abs.exists():
        raise FileNotFoundError(f"메쉬 파일을 찾을 수 없습니다: {mesh_abs}")
    
    # 출력 디렉토리는 미리 만들어 두는 편이 안전
    out_abs.mkdir(parents=True, exist_ok=True)

    cmd = [
        str(blender_exec),
        "-b",
        "-P", str(script_path),
        "--",
        "--mesh_dir", str(mesh_abs),
        "--output_dir", str(out_abs)
    ]
    print(cmd)

    try:
        result = subprocess.run(
            cmd,
            check=True,
            capture_output=True,
            text=True,
            cwd=base_dir
        )
        print("=== Blender stdout ===")
        print(result.stdout)
        print("=== Blender stderr ===")
        print(result.stderr)
    except subprocess.CalledProcessError as e:
        print(f"Blender 실행에 실패했습니다 (return code: {e.returncode})")
        print("stdout:", e.stdout)
        print("stderr:", e.stderr)
        raise

if __name__ == "__main__":
    run_blender(
        mesh_dir="../outputs/mesh_segmentation_output/CustomDataset/000-001/000234d39e684deb80b7b8d028681dc1/000234d39e684deb80b7b8d028681dc1_label_132.glb",
        output_dir="../outputs/mesh_segmentation_output/CustomDataset/000-001/000234d39e684deb80b7b8d028681dc1/renders",
        blender_path="./blender-3.4.1-linux-x64/blender",
        script_relpath="blender_render_script_type1.py"
    )

/home/user/ys/mesh_reasoning/samesh/outputs/mesh_segmentation_output/CustomDataset/000-001/000234d39e684deb80b7b8d028681dc1/000234d39e684deb80b7b8d028681dc1_label_132.glb
/home/user/ys/mesh_reasoning/samesh/outputs/mesh_segmentation_output/CustomDataset/000-001/000234d39e684deb80b7b8d028681dc1/renders
['blender-3.4.1-linux-x64/blender', '-b', '-P', '/home/user/ys/mesh_reasoning/samesh/notebooks/blender_render_script_type1.py', '--', '--mesh_dir', '/home/user/ys/mesh_reasoning/samesh/outputs/mesh_segmentation_output/CustomDataset/000-001/000234d39e684deb80b7b8d028681dc1/000234d39e684deb80b7b8d028681dc1_label_132.glb', '--output_dir', '/home/user/ys/mesh_reasoning/samesh/outputs/mesh_segmentation_output/CustomDataset/000-001/000234d39e684deb80b7b8d028681dc1/renders']
=== Blender stdout ===
Blender 3.4.1 (hash 55485cb379f7 built 2022-12-20 00:46:45)
/run/user/1000/gvfs/ non-existent directory
/home/user/ys/mesh_reasoning/samesh/outputs/mesh_segmentation_output/CustomDataset/000-001/000234